# Практикум 1. Поиск в PDB и основы визуализации

Условия запроса:
*   Ключевые слова: androgen
*   Где они должны быть: в заголовке
*   Дата публикации записи: с января 2005 по январь 2010 года
*   Какое разрешение: не хуже 2,6 ангстрем
*   Сколько лигандов должно быть в записи: не меньше 2

## Установка и импорт необходимого пакета

In [1]:
!pip install nglview --user
import nglview as nv
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


## Задание 1

Создаю заготовку поискового запроса

In [2]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

Добавляю в запрос условие наличия ключевого слова "androgen" в заголовке

In [3]:
keyword_clause = {
    "type": "terminal",
    "service": "text", # Сервис поиска в определенном поле записи
    "parameters": {
        "value": "androgen",
        "attribute": "struct.title", # В данном случае это поле -- заголовок записи
        "operator": "contains_words" # Должны присутствовать какие-то слова 
    }
}

my_query["query"]["nodes"].append(keyword_clause)

Добавляю в запрос условие разрешения не хуже 2,6 ангстрем

In [4]:
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.6,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

Добавляю в запрос условие количества лигандов не меньше 2

In [5]:
has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 1,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

Добавляю в запрос условие даты публикации записи с января 2005 по январь 2010 года

In [6]:
date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2005-01-01",
            "to": "2010-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

Отправляю сформированный запрос на сервер

In [7]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query)
search = requests.post(f'{rcsb}', data=json_query)

Проверяю ответ сервера, если код 200, значит всё прошло правильно

In [8]:
search

<Response [200]>

In [9]:
search_result = search.json() # Распаковываем ответ сервера в словарь
search_result

{'query_id': 'b1645268-6fb1-40bf-a52b-f461cf2b83e6',
 'result_type': 'entry',
 'total_count': 18,
 'result_set': [{'identifier': '2PIV',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 1127,
       'original_score': 209.43798828125,
       'norm_score': 1.0}]}]},
  {'identifier': '2PIW',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 1127,
       'original_score': 209.43798828125,
       'norm_score': 1.0}]}]},
  {'identifier': '2PIO',
   'score': 0.8375189317794275,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 1127,
       'original_score': 200.59506225585938,
       'norm_score': 0.8375189317794275}]}]},
  {'identifier': '2PIP',
   'score': 0.8375189317794275,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 1127,
       'original_score': 200.59506225585938,
       'norm_score': 0.8375189317794275}]}]},
  {'identifier': '2PIQ',
   'score': 0.8375189317794275,
   'servi

In [10]:
best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '2PIV',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 1127,
     'original_score': 209.43798828125,
     'norm_score': 1.0}]}]}

## Задание 2

Идентиификатору 2PIV соответствует рецептор андрогена, который играет центральную роль при раке предстательной железы. В качестве лиганда имеется трийодтиронин -- гормон щитовидной железы, который может связываться с ранее неизвестным BF-3 и ингибировать рецептор андрогена за счёт реконструирования соседнего участка BF-2, что ослабляет его связывание с коактиватором.

## Задание 3

Код для создания интерактивной ячейки jupyter notebook, позволяющей выбирать варианты отображения 1, 7 и 8.

In [11]:
from ipywidgets import interact, fixed

In [12]:
my_examples = {
    'Отображение 1': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде rope красного цвета
Боковые радикалы в стержневой модели, покрашенные согласно элементу
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity': 0.1
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': 'red'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
        ],
    },
    'Отображение 2': {
        'description': '''
Белок в виде ribbon, покрашенной градиентом от N к C концу
Боковые радикалы в стержневой модели, покрашенные по элементам
Углероды гидрофобных аминокислот покрашены в светло-желтый
Углероды полярных заряженных аминокислот покрашены в светло-голубой
Лиганды не показаны никак
''',
        'representations': [
            {
                'type': 'ribbon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'residueindex'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'hydrophobic and _C',                     
                    'color': 'lightyellow'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'polar and _C',                     
                    'color': 'lightblue'  
                 }
            },
        ],
    },
    'Отображение 3': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде cartoon темно-серого цвета
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity': 0.1
                 }
            },
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',                     
                    'color': 'darkgray'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'hydrophobicity'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
        ],
    },
}

In [13]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("2PIV", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Отображение 1', 'Отображение 2', 'Отображ…

NGLWidget()